In [110]:
from desdeo.problem.testproblems.single_objective import (
    new_branin_function,
    mystery_function,
    mishras_bird_constrained,
    rosenbrock_disk,
    townsend_modified,
)
from desdeo.problem.testproblems import dtlz2
from desdeo.emo.hooks.archivers import NonDominatedArchive
from desdeo.emo.methods.EAs import ReferenceVectorOptions, nsga3, rvea
from desdeo.emo.hooks.archivers import Archive
from desdeo.emo.operators.selection import ReferenceVectorOptions
from desdeo.emo import algorithms, crossover, mutation, scalar_selection, selection, termination, generator
from desdeo.tools import NevergradGenericOptions, NevergradGenericSolver
from desdeo.problem import Objective, Problem
import plotly.graph_objects as go
import polars as pl
import numpy as np
from desdeo.problem.external.pymoo_provider import PymooProblemParams, create_pymoo_problem


In [111]:
# Setup the problem, set the constraint as an objective
problem = create_pymoo_problem(PymooProblemParams(name="pressure_vessel"))
# problem = rosenbrock_disk()
# problem = new_branin_function()
# problem = townsend_modified()
problem

Problem(name='PressureVessel', description='The PressureVessel problem as defined in the Pymoo library.', constants=None, variables=[Variable(name='x_1', symbol='x_1', variable_type=<VariableTypeEnum.real: 'real'>, lowerbound=1.0, upperbound=99.0, initial_value=None), Variable(name='x_2', symbol='x_2', variable_type=<VariableTypeEnum.real: 'real'>, lowerbound=1.0, upperbound=99.0, initial_value=None), Variable(name='x_3', symbol='x_3', variable_type=<VariableTypeEnum.real: 'real'>, lowerbound=10.0, upperbound=200.0, initial_value=None), Variable(name='x_4', symbol='x_4', variable_type=<VariableTypeEnum.real: 'real'>, lowerbound=10.0, upperbound=200.0, initial_value=None)], objectives=[Objective(description=None, name='f_1', symbol='f_1', unit=None, func=None, simulator_path=Url(url='desdeo://external/pymoo/evaluate', auth=None), surrogates=None, maximize=False, ideal=5885.3, nadir=5885.3, objective_type=<ObjectiveTypeEnum.simulator: 'simulator'>, is_linear=False, is_convex=False, is_tw

In [112]:
def objective_from_constraint(problem: Problem, constraint_symbol: str) -> Objective:
    """Create an Objective that evaluates exactly like the given constraint.

    Works for both analytic constraints (func != None) and simulator-backed constraints
    (func is None but simulator_path is set).
    """
    cons = problem.get_constraint(constraint_symbol)

    if cons.func is not None:
        return Objective(
            name=f"Constraint_{constraint_symbol}",
            symbol=constraint_symbol,
            func=cons.func,
        )

    # Simulator-backed constraint (e.g., pymoo external problems)
    if getattr(cons, "simulator_path", None) is not None:
        return Objective(
            name=f"Constraint_{constraint_symbol}",
            symbol=constraint_symbol,
            func=None,
            simulator_path=cons.simulator_path,
            objective_type="simulator",
        )

    raise ValueError(
        f"Constraint '{constraint_symbol}' has neither 'func' nor 'simulator_path'. Cannot promote to objective."
    )


def setup_problem(problem: Problem, constraint_symbols: list[str]) -> Problem:
    """Takes a single-objective optimization problem and setups one...

    Takes a single-objective optimization problem and setups one of its constraints as its second objective function.
    """
    extra_objectives = [objective_from_constraint(problem, sym) for sym in constraint_symbols]
    return problem.model_copy(
        update={
            "constraints": None,
            "objectives": [*problem.objectives, *extra_objectives],
        }
    )


def generate_front(
    problem: Problem,
    xover_probability: float,
    xover_distribution: float,
    distribution_index: float,
    tournament_size: int,
    population_size: int,
    n_generations: int,
) -> NonDominatedArchive:
    """Run NSGA2 to generate a front for a given problem."""
    # setup
    nsga2_options = algorithms.nsga2_options()

    nsga2_options.template.crossover = crossover.SimulatedBinaryCrossoverOptions(
        xover_probability=xover_probability, xover_distribution=xover_distribution
    )
    nsga2_options.template.mutation = mutation.BoundedPolynomialMutationOptions(
        mutation_probability=1.0 / len(problem.variables), distribution_index=distribution_index
    )
    nsga2_options.template.mate_selection = scalar_selection.TournamentSelectionOptions(
        name="TournamentSelection", tournament_size=tournament_size, winner_size=population_size
    )

    nsga2_options.template.generator = generator.LHSGeneratorOptions(n_points=population_size)
    nsga2_options.template.termination = termination.MaxGenerationsTerminatorOptions(max_generations=n_generations)

    solver, extras = algorithms.emo_constructor(emo_options=nsga2_options, problem=problem)

    _ = solver()

    return extras.archive


def generate_front_nsga3(
    problem: Problem,
    xover_probability: float,
    xover_distribution: float,
    distribution_index: float,
    tournament_size: int,
    population_size: int,
    n_generations: int,
) -> NonDominatedArchive:
    """Run NSGA3 to generate a front for a given problem."""
    # setup
    nsga3_options = algorithms.nsga3_options()

    nsga3_options.template.crossover = crossover.SimulatedBinaryCrossoverOptions(
        xover_probability=xover_probability, xover_distribution=xover_distribution
    )
    nsga3_options.template.mutation = mutation.BoundedPolynomialMutationOptions(
        mutation_probability=1.0 / len(problem.variables), distribution_index=distribution_index
    )
    nsga3_options.template.selection = selection.NSGA3SelectorOptions(
        reference_vector_options=ReferenceVectorOptions(
            number_of_vectors=population_size,
            # reference_point={"f_1": -0.80361910412559, "c_1": 0.0, "c_2": 0.0}
        )
    )

    nsga3_options.template.generator = generator.LHSGeneratorOptions(n_points=population_size)
    nsga3_options.template.termination = termination.MaxGenerationsTerminatorOptions(max_generations=n_generations)

    solver, extras = algorithms.emo_constructor(emo_options=nsga3_options, problem=problem)

    _ = solver()

    return extras.archive

In [113]:
# problem = setup_problem(problem, ["c_1", "c_2", "c_3", "c_4", "c_5", "c_6"])
problem = setup_problem(problem, ["c_1", "c_2", "c_3", "c_4"])
# problem = setup_problem(problem, ["c_1", "c_2"])


# solve the problem
pop_size = 100
n_gen = 2000
archive = generate_front_nsga3(problem, 0.9, 20, 20, 2, pop_size, n_gen)
# to_plot = result.optimal_outputs
to_plot = archive.solutions
to_plot

shape: (135_115, 15)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ x_1       ┆ x_2       ┆ x_3       ┆ x_4       ┆ … ┆ c_2_min   ┆ c_3_min   ┆ c_4_min   ┆ generati │
│ ---       ┆ ---       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ on       │
│ f64       ┆ f64       ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ ---      │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ i32      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 8.081523  ┆ 41.729899 ┆ 86.268664 ┆ 194.87500 ┆ … ┆ -0.595039 ┆ -4.59078  ┆ -0.188021 ┆ 1        │
│           ┆           ┆           ┆ 1         ┆   ┆           ┆           ┆           ┆          │
│ 53.827706 ┆ 51.00389  ┆ 52.253835 ┆ 130.10647 ┆ … ┆ -0.896414 ┆ -0.322298 ┆ -0.45789  ┆ 1        │
│           ┆           ┆           ┆ 8         ┆   ┆           ┆           ┆           ┆          │
│ 35.174449 ┆ 31.918622 ┆ 151.79548 ┆ 122.23914 ┆ … ┆ -0.182262 ┆ -17.13240 ┆ -0.49067  ┆ 1        │
│           ┆           ┆ 4         ┆ 7         ┆   ┆           ┆ 5         ┆           ┆          │
│ 24.869012 ┆ 95.253694 ┆ 178.25751 ┆ 98.868246 ┆ … ┆ -1.417593 ┆ -24.92290 ┆ -0.588049 ┆ 1        │
│           ┆           ┆ 3         ┆           ┆   ┆           ┆ 2         ┆           ┆          │
│ 81.796507 ┆ 55.817459 ┆ 164.22750 ┆ 170.29983 ┆ … ┆ -0.64062  ┆ -24.44997 ┆ -0.290417 ┆ 1        │
│           ┆           ┆ 1         ┆ 8         ┆   ┆           ┆ 7         ┆           ┆          │
│ …         ┆ …         ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ 1.0       ┆ 59.543674 ┆ 10.0      ┆ 11.439087 ┆ … ┆ -1.208693 ┆ 0.993995  ┆ -0.952337 ┆ 2000     │
│ 69.622864 ┆ 97.818917 ┆ 133.02932 ┆ 10.0      ┆ … ┆ -1.614861 ┆ -7.037951 ┆ -0.958333 ┆ 2000     │
│           ┆           ┆ 8         ┆           ┆   ┆           ┆           ┆           ┆          │
│ 94.620754 ┆ 68.052778 ┆ 181.77244 ┆ 10.79193  ┆ … ┆ -0.83973  ┆ -19.27625 ┆ -0.955034 ┆ 2000     │
│           ┆           ┆ 5         ┆           ┆   ┆           ┆ 8         ┆           ┆          │
│ 97.572851 ┆ 98.164696 ┆ 190.45432 ┆ 114.91034 ┆ … ┆ -1.439453 ┆ -31.43214 ┆ -0.521207 ┆ 2000     │
│           ┆           ┆ 5         ┆ 4         ┆   ┆           ┆ 6         ┆           ┆          │
│ 52.206467 ┆ 14.104778 ┆ 200.0     ┆ 199.43116 ┆ … ┆ 0.34215   ┆ -44.19412 ┆ -0.169037 ┆ 2000     │
│           ┆           ┆           ┆ 2         ┆   ┆           ┆ 1         ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [115]:
feasible = to_plot.with_columns(
    # pl.when((pl.col("c_1") <= 0.0) & (pl.col("c_2") <= 0.0))
    pl.when((pl.col("c_1") <= 0.0) & (pl.col("c_2") <= 0) & (pl.col("c_3") <= 0) & (pl.col("c_4") <= 0))
    .then(pl.col("f_1_min"))
    .otherwise(float("inf"))
    .alias("feasible_f_1")
)

best_by_gen = (
    feasible.group_by("generation").agg(pl.col("feasible_f_1").min().alias("best_f_1_this_gen")).sort("generation")
)

feasible.sort("feasible_f_1")

shape: (135_115, 16)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ x_1       ┆ x_2       ┆ x_3       ┆ x_4       ┆ … ┆ c_3_min   ┆ c_4_min   ┆ generatio ┆ feasible │
│ ---       ┆ ---       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ n         ┆ _f_1     │
│ f64       ┆ f64       ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ ---       ┆ ---      │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ i32       ┆ f64      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 18.120294 ┆ 10.436962 ┆ 51.1273   ┆ 95.455082 ┆ … ┆ -0.036811 ┆ -0.60227  ┆ 1803      ┆ 8160.624 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 489      │
│ 28.858237 ┆ 10.533187 ┆ 65.693186 ┆ 10.0      ┆ … ┆ -0.020928 ┆ -0.958333 ┆ 1549      ┆ 10132.10 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 7232     │
│ 28.597499 ┆ 15.828525 ┆ 65.988612 ┆ 10.0      ┆ … ┆ -0.034288 ┆ -0.958333 ┆ 1550      ┆ 12677.39 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 1955     │
│ 29.285981 ┆ 7.713027  ┆ 42.156605 ┆ 196.64025 ┆ … ┆ -0.089275 ┆ -0.180666 ┆ 443       ┆ 15855.07 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 8049     │
│ 22.300207 ┆ 29.100616 ┆ 69.469449 ┆ 11.162091 ┆ … ┆ -0.214171 ┆ -0.953491 ┆ 1839      ┆ 19025.95 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 488      │
│ …         ┆ …         ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ 1.0       ┆ 89.605118 ┆ 200.0     ┆ 193.10407 ┆ … ┆ -43.58062 ┆ -0.1954   ┆ 2000      ┆ inf      │
│           ┆           ┆           ┆           ┆   ┆ 9         ┆           ┆           ┆          │
│ 1.0       ┆ 43.345723 ┆ 199.59715 ┆ 37.331637 ┆ … ┆ -28.30601 ┆ -0.844452 ┆ 2000      ┆ inf      │
│           ┆           ┆ 5         ┆           ┆   ┆ 1         ┆           ┆           ┆          │
│ 1.0       ┆ 1.0       ┆ 167.01737 ┆ 12.547895 ┆ … ┆ -14.90652 ┆ -0.947717 ┆ 2000      ┆ inf      │
│           ┆           ┆ 6         ┆           ┆   ┆           ┆           ┆           ┆          │
│ 1.0       ┆ 59.543674 ┆ 10.0      ┆ 11.439087 ┆ … ┆ 0.993995  ┆ -0.952337 ┆ 2000      ┆ inf      │
│ 52.206467 ┆ 14.104778 ┆ 200.0     ┆ 199.43116 ┆ … ┆ -44.19412 ┆ -0.169037 ┆ 2000      ┆ inf      │
│           ┆           ┆           ┆ 2         ┆   ┆ 1         ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [119]:
# plot

fig = go.Figure(go.Scatter(x=to_plot["f_1"], y=to_plot["c_1"], mode="markers", name="solutions"))
# fig.add_vline(x=-0.80361910412559, line_dash="dot", line_width=1.0, line_color="red", name="True optima")
# fig.add_hline(y=-6961.81387558015, line_dash="dot", line_width=1.0, line_color="red", name="c_1 value at true optima")
fig.update_layout(xaxis_title="f_1", yaxis_title="c_1", title="Objective vs Constraint")
fig.show(renderer="notebook", include_plotlyjs="cdn")


In [121]:
best_so_far = best_by_gen["best_f_1_this_gen"].cum_min()
best_by_gen = best_by_gen.with_columns(pl.Series("best_f_1_so_far", best_so_far))

best_by_gen

shape: (2_000, 3)
┌────────────┬───────────────────┬─────────────────┐
│ generation ┆ best_f_1_this_gen ┆ best_f_1_so_far │
│ ---        ┆ ---               ┆ ---             │
│ i32        ┆ f64               ┆ f64             │
╞════════════╪═══════════════════╪═════════════════╡
│ 1          ┆ 43237.268546      ┆ 43237.268546    │
│ 2          ┆ 32611.821202      ┆ 32611.821202    │
│ 3          ┆ 20813.980193      ┆ 20813.980193    │
│ 4          ┆ 40730.940574      ┆ 20813.980193    │
│ 5          ┆ 39348.750716      ┆ 20813.980193    │
│ …          ┆ …                 ┆ …               │
│ 1996       ┆ 120367.218065     ┆ 8160.624489     │
│ 1997       ┆ 83126.799429      ┆ 8160.624489     │
│ 1998       ┆ 116769.126077     ┆ 8160.624489     │
│ 1999       ┆ 88046.753469      ┆ 8160.624489     │
│ 2000       ┆ 134252.827543     ┆ 8160.624489     │
└────────────┴───────────────────┴─────────────────┘

In [122]:
fig = go.Figure(
    go.Scatter(
        x=best_by_gen["generation"],
        y=best_by_gen["best_f_1_so_far"],
        mode="lines+markers",
        name="Best feasible f_1_min so far",
    )
)

fig.update_layout(
    title="Best feasible f_1_min vs Generation",
    xaxis_title="Generation",
    yaxis_title="Best feasible f_1_min so far",
)

fig.show()